# Fitness Function

In [22]:
#import tensorflow as tf
import numpy as np
import pandas as pd
from sklearn import preprocessing
from keras.models import Sequential, load_model
from keras.layers.core import Dense, Dropout
from keras.layers.recurrent import LSTM

def normalize(df):#標準化Ｋ
    newdf= df.copy()
    min_max_scaler = preprocessing.MinMaxScaler()
    for feature in df.columns:
        newdf[feature] = min_max_scaler.fit_transform(df[feature].values.reshape(-1,1))
    return newdf

def data_helper(df, time_frame,TRAIN_RATE):
    # Feature number
    number_features = len(df.columns)
    datavalue = df.as_matrix() #66個x(column) * 918個時間(row)，(每一個時有66個x) , [[66x],[66x],....[66x]]
    x_result = []    
    y_result = []
    for index in range(len(datavalue)-time_frame):
        x_result.append(datavalue[index: index + time_frame])
        y_result.append(datavalue[index + time_frame][4])  # test for closeprice 加time_step後的closeprice，如果要預測其他的y要改這裡
    # 每五天(time_step)當一個x 
    #[ [[1st 66x],[2nd 66x],[3rd 66x],[4th 66x],[5th 66x]] , [[2nd 66x],[3rd 66x],[4th 66x],[5th 66x],[6th 66x]] ,....]
    x_result = np.array(x_result)
    y_result = np.array(y_result)#第time_step+1的closeprice當做y

    number_train = round(TRAIN_RATE * x_result.shape[0])
    #一次切二個list(x_train & x_test),x_train為0~number_train ->[:number_train],x_text為number_train~final ->[number_train:]
    x_train, x_test = x_result[:int(number_train)], x_result[int(number_train) :]
    y_train, y_test = y_result[:int(number_train)], y_result[int(number_train) :]
    
    x_train = np.reshape(x_train, (x_train.shape[0], x_train.shape[1], number_features))
    x_test = np.reshape(x_test, (x_test.shape[0], x_test.shape[1], number_features))
    return [x_train, y_train, x_test, y_test]

def build_model(input_length, input_dim,LAYERS_NUM,CELL_SIZE,DROPOUT_RATE):
    model = Sequential()
    for _ in range(LAYERS_NUM):
        model.add(LSTM(CELL_SIZE, input_shape=(input_length, input_dim), return_sequences=True))
        model.add(Dropout(DROPOUT_RATE))
    model.add(LSTM(CELL_SIZE, input_shape=(input_length, input_dim), return_sequences=False))
    model.add(Dropout(DROPOUT_RATE))
    model.add(Dense(16,kernel_initializer="uniform",activation='relu'))
    model.add(Dense(1,kernel_initializer="uniform",activation='linear')) # CELL_SIZE 5, output dim
    model.compile(loss='mse',optimizer='adam', metrics=['accuracy'])
    return model

def denormalize(df, norm_value):
    original_value = df['ClosePrice'].values.reshape(-1,1)
    norm_value = norm_value.reshape(-1,1)

    min_max_scaler = preprocessing.MinMaxScaler()
    min_max_scaler.fit_transform(original_value)
    denorm_value = min_max_scaler.inverse_transform(norm_value)
    return denorm_value

def LSTM_model(chromosom):
    # Load files
    foxconndf= pd.read_csv('0051.csv', index_col=0 )
    foxconndf.dropna(how='any',inplace=True)#把date那欄刪掉?
    FEATURE_NUM = len(foxconndf.columns)

    TIME_STEPS = chromosom[0] #要用幾天來預測
    TRAIN_RATE = chromosom[1]#train 資料要用多少%
    CELL_SIZE = chromosom[2]
    LAYERS_NUM = chromosom[3] #隱藏層數? 還是total層數??
    BATCH_SIZE = chromosom[4]
    EPOCHS_NUM = chromosom[5] #迭代數
    DROPOUT_RATE = chromosom[6] #每層要drop多少%
    activation_1=chromosom[7]
    activation_2=chromosom[8]
    validation_rate=chromosom[9]

    foxconndf_norm= normalize(foxconndf)

    X_train, y_train, X_test, y_test = data_helper(foxconndf_norm, TIME_STEPS,TRAIN_RATE)

    data_helper(foxconndf_norm, TIME_STEPS,TRAIN_RATE)

    model = build_model( TIME_STEPS, FEATURE_NUM,LAYERS_NUM,CELL_SIZE,DROPOUT_RATE )
    model.fit( X_train, y_train, batch_size=BATCH_SIZE, epochs=EPOCHS_NUM, validation_split=0.1, verbose=1)
    train_history=model.fit( X_train, y_train, batch_size=BATCH_SIZE, epochs=EPOCHS_NUM, validation_split=0.1, verbose=1)

    pred = model.predict(X_test) # model.predict(data set)

    denorm_pred = denormalize(foxconndf, pred)
    denorm_ytest = denormalize(foxconndf, y_test)
    # print(model.summary()) # model summary
    # print(model.get_config()) # model configuration
    model.save('model_test_closeonly.h1')
    my_model = load_model('model_test_closeonly.h1')
    score = model.evaluate(X_train, y_train, batch_size=BATCH_SIZE)
    return score[0]



# GA Function

In [23]:
chromosom_value=[[10,20,30],[0.1,0.2,0.3],[16,32,64,128,256],[1,2,3],[100,200,300],[100,200,300],[0.1,0.2,0.3,0.4,0.5],["sigmoid","relu","linear"],["sigmoid","relu","linear"],[0.1,0.2,0.3]]

import random
def createrandomList(create_number,category):
    list_random = [ random.randint(0,category) for i in range(create_number)]
    return(list_random)

#init create population chromosome(100)--function input：filename & population, output：population_list 
def create_population(population):
    population_list=[]
    for popu in range(population):
        chromosome_create=[]
        for index in chromosom_value:
            chromosome_create.append(index[createrandomList(1,len(index)-1)[0]]) #從chromosom_value隨機產生一個值塞到
        population_list.append(chromosome_create)
    return population_list

def cross(cross_rate,chromosome_1,chromosome_2):
    random_rate=random.random()
    if(random_rate>cross_rate):
        point_1=random.randint(0,len(chromosome_1)-1)
        point_2=random.randint(0,len(chromosome_1)-1)

        while(point_1>=point_2):
            point_1=random.randint(0,len(chromosome_1)-1)
            point_2=random.randint(0,len(chromosome_1)-1)

        print("cross_point1: "+str(point_1))
        print("cross_point2: "+str(point_2))
#         print("cross_len_chromosome_1= "+str(len(chromosome_1)))
#         print("cross_len_chromosome_2= "+str(len(chromosome_2)))

        tmp=0
        for index in range(point_1,point_2+1):
            tmp=chromosome_1[index]
            chromosome_1[index]=chromosome_2[index]
            chromosome_2[index]=tmp
    return chromosome_1

def mutation(mutation_rate,chromosome):
    random_rate=random.random()
    if(random_rate>mutation_rate):
        print("mutation_start")
        point_1=random.randint(0,len(chromosome)-1)#產生二個隨機point1 & point2 為了到時候mutation
        point_2=random.randint(0,len(chromosome)-1)
        while(point_1==point_2):#如果point1 point2 一樣要重新產生
            point_1=random.randint(0,len(chromosome)-1)
            point_2=random.randint(0,len(chromosome)-1)
        print("mu_point1= "+str(point_1))
        print("mu_point2= "+str(point_2))

        tmp=chromosome[point_1]#改變染色體中第point1的值，如果產生的新值與舊的一樣要再重新產生
        #chromosome[point_1]值等於chromosom_value裡面隨機產生的一個值createrandomList(1,len(chromosom_value[point_1])-1)[0]
        chromosome[point_1]=chromosom_value[point_1][createrandomList(1,len(chromosom_value[point_1])-1)[0]]#
        while(tmp==chromosome[point_1]):
            chromosome[point_1]=chromosom_value[point_1][createrandomList(1,len(chromosom_value[point_1])-1)[0]]

        tmp_2=chromosome[point_2]#改變染色體中第point2的值，如果產生的新值與舊的一樣要再重新產生
        chromosome[point_2]=chromosom_value[point_2][createrandomList(1,len(chromosom_value[point_2])-1)[0]]
        while(tmp_2==chromosome[point_2]):
            chromosome[point_2]=chromosom_value[point_2][createrandomList(1,len(chromosom_value[point_2])-1)[0]]
    return chromosome

def calculateY_rank(rank_number,population_list):
    result_all_x_fitness=[]#記錄所有population與產生的y
    best_result=[]#記錄最好的population&y
    
    # 調整 foxconndf columns
#     test = [5,0.1,50,2,None,100,0.3,'relu','linear', 0.1] # 參數list範例
#     score = generate_model(test, foxconndf, '0051.csv')
    
    for index in population_list:
        fitness_value=LSTM_model(index)#calculate fintness_value
        result_all_x_fitness.append([fitness_value,index])
    
    result_rank=[]#record before rank"s x & fitness_value
    for index in range(0,rank_number):
        result_rank.append(sorted(result_all_x_fitness,reverse=True)[index])#sort:big->small
    best_result=result_rank[0]
    
    x_final=[]#記錄前十五名的染色體
    for index in result_rank:
        x_final.append(index[1])
    return [x_final,best_result]

#產生新的X(上一代最好的前15個交配+突變產生新的15個+隨機產生85個新的x)--function
def create_new_x(rank_number,population,cross_rate,mutation_rate,x_final):
    new_x=[]
    #先把前15名的染色體做交配&突變->產生新15個染色體
    for index in range(0,rank_number):
        other_ch=createrandomList(1,rank_number-1)[0]
        while(index==other_ch):
            other_ch=createrandomList(1,rank_number-1)[0] #變矩陣要減1 if index= other_ch -> create other_ch again
        print("i_th chromosome: "+str(index))
        print("other_random_chromosome: "+str(other_ch))
        cross_result=cross(cross_rate,x_final[index],x_final[other_ch])
        new_x.append(mutation(mutation_rate,cross_result))

    #隨機產生第16~100的染色體
    for index in range(0,population-rank_number):
        new_x.append(create_population(1)[0])
    return new_x

# Main: LSTM_output1 +GA

In [ ]:
#GA + regression ->main
import datetime
#init parameter
iteration=30
iteration_now=0
population=10
rank_number=5

cross_rate=0.1
mutation_rate=0.1

y_target=0#fitnessvalue的目標，到達就停止迭代->望小
y_best=100000#目前為止(所有迭代中)最好的fitnessvalue
y_now=100000#當前此迭代中最好的fitnessvalue
x_best=[]

population_list=create_population(population)#產生初始母體染色體

Totalstarttime=datetime.datetime.now()
print("Start GA: "+str(Totalstarttime))
while(not(iteration_now>=iteration or y_best<y_target)):
    iteration_now=iteration_now+1
    print("\niteration_now= "+str(iteration_now))
    Y=calculateY_rank(rank_number,population_list) #return X_final(前15名的染色體) & best_result(此代最好的fitness跟染色體)
    y_now=Y[1][0]
    print("y_now= "+str(y_now))
    if y_now<y_best:
        y_best=y_now
        print("y_best= "+str(y_best))
        x_best=Y[1][1]
        #print("x_best= "+str(x_best))
    population_list=create_new_x(rank_number,population,cross_rate,mutation_rate,Y[0])

print("iteration_now= "+str(iteration_now))
print("y_best= "+str(y_best))
print("x_best= "+str(x_best))

print("GA's end time is "+str(datetime.datetime.now()))
print("All time spends:  "+str(datetime.datetime.now()-Totalstarttime))

Start GA: 2018-05-20 23:33:35.960875

iteration_now= 1
Train on 267 samples, validate on 30 samples
Epoch 1/100
267/267 [==============================] - 2s 7ms/step - loss: 0.3763 - acc: 0.0000e+00 - val_loss: 0.4194 - val_acc: 0.0000e+00
Epoch 2/100
267/267 [==============================] - 0s 1ms/step - loss: 0.1440 - acc: 0.0000e+00 - val_loss: 0.0652 - val_acc: 0.0000e+00
Epoch 3/100
267/267 [==============================] - 0s 1ms/step - loss: 0.0326 - acc: 0.0000e+00 - val_loss: 0.0019 - val_acc: 0.0000e+00
Epoch 4/100
267/267 [==============================] - 0s 1ms/step - loss: 0.0395 - acc: 0.0000e+00 - val_loss: 0.0358 - val_acc: 0.0000e+00
Epoch 5/100
267/267 [==============================] - 0s 994us/step - loss: 0.0187 - acc: 0.0000e+00 - val_loss: 0.0941 - val_acc: 0.0000e+00
Epoch 6/100
267/267 [==============================] - 0s 981us/step - loss: 0.0279 - acc: 0.0000e+00 - val_loss: 0.1019 - val_acc: 0.0000e+00
Epoch 7/100
267/267 [=============================

267/267 [==============================] - 0s 1ms/step - loss: 0.0020 - acc: 0.0000e+00 - val_loss: 0.0086 - val_acc: 0.0000e+00
Epoch 15/100
267/267 [==============================] - 0s 1ms/step - loss: 0.0018 - acc: 0.0000e+00 - val_loss: 0.0048 - val_acc: 0.0000e+00
Epoch 16/100
267/267 [==============================] - 0s 996us/step - loss: 0.0019 - acc: 0.0000e+00 - val_loss: 0.0086 - val_acc: 0.0000e+00
Epoch 17/100
267/267 [==============================] - 0s 990us/step - loss: 0.0017 - acc: 0.0000e+00 - val_loss: 0.0054 - val_acc: 0.0000e+00
Epoch 18/100
267/267 [==============================] - 0s 973us/step - loss: 0.0020 - acc: 0.0000e+00 - val_loss: 0.0079 - val_acc: 0.0000e+00
Epoch 19/100
267/267 [==============================] - 0s 1ms/step - loss: 0.0018 - acc: 0.0000e+00 - val_loss: 0.0056 - val_acc: 0.0000e+00
Epoch 20/100
267/267 [==============================] - 0s 1ms/step - loss: 0.0017 - acc: 0.0000e+00 - val_loss: 0.0081 - val_acc: 0.0000e+00
Epoch 21/100


89/89 [==============================] - 0s 203us/step - loss: 0.1427 - acc: 0.0000e+00 - val_loss: 0.2387 - val_acc: 0.0000e+00
Epoch 29/200
89/89 [==============================] - 0s 174us/step - loss: 0.1340 - acc: 0.0000e+00 - val_loss: 0.2279 - val_acc: 0.0000e+00
Epoch 30/200
89/89 [==============================] - 0s 174us/step - loss: 0.1264 - acc: 0.0000e+00 - val_loss: 0.2167 - val_acc: 0.0000e+00
Epoch 31/200
89/89 [==============================] - 0s 158us/step - loss: 0.1149 - acc: 0.0000e+00 - val_loss: 0.2052 - val_acc: 0.0000e+00
Epoch 32/200
89/89 [==============================] - 0s 169us/step - loss: 0.1110 - acc: 0.0000e+00 - val_loss: 0.1932 - val_acc: 0.0000e+00
Epoch 33/200
89/89 [==============================] - 0s 158us/step - loss: 0.1007 - acc: 0.0000e+00 - val_loss: 0.1810 - val_acc: 0.0000e+00
Epoch 34/200
89/89 [==============================] - 0s 152us/step - loss: 0.0934 - acc: 0.0000e+00 - val_loss: 0.1685 - val_acc: 0.0000e+00
Epoch 35/200
89/89 

Epoch 86/200
89/89 [==============================] - 0s 174us/step - loss: 0.0124 - acc: 0.0000e+00 - val_loss: 0.0217 - val_acc: 0.0000e+00
Epoch 87/200
89/89 [==============================] - 0s 174us/step - loss: 0.0114 - acc: 0.0000e+00 - val_loss: 0.0210 - val_acc: 0.0000e+00
Epoch 88/200
89/89 [==============================] - 0s 158us/step - loss: 0.0135 - acc: 0.0000e+00 - val_loss: 0.0205 - val_acc: 0.0000e+00
Epoch 89/200
89/89 [==============================] - 0s 152us/step - loss: 0.0117 - acc: 0.0000e+00 - val_loss: 0.0200 - val_acc: 0.0000e+00
Epoch 90/200
89/89 [==============================] - 0s 163us/step - loss: 0.0109 - acc: 0.0000e+00 - val_loss: 0.0196 - val_acc: 0.0000e+00
Epoch 91/200
89/89 [==============================] - 0s 174us/step - loss: 0.0106 - acc: 0.0000e+00 - val_loss: 0.0195 - val_acc: 0.0000e+00
Epoch 92/200
89/89 [==============================] - 0s 163us/step - loss: 0.0106 - acc: 0.0000e+00 - val_loss: 0.0196 - val_acc: 0.0000e+00
Epoch 

Epoch 144/200
89/89 [==============================] - 0s 225us/step - loss: 0.0105 - acc: 0.0000e+00 - val_loss: 0.0211 - val_acc: 0.0000e+00
Epoch 145/200
89/89 [==============================] - 0s 141us/step - loss: 0.0111 - acc: 0.0000e+00 - val_loss: 0.0207 - val_acc: 0.0000e+00
Epoch 146/200
89/89 [==============================] - 0s 163us/step - loss: 0.0086 - acc: 0.0000e+00 - val_loss: 0.0203 - val_acc: 0.0000e+00
Epoch 147/200
89/89 [==============================] - 0s 191us/step - loss: 0.0094 - acc: 0.0000e+00 - val_loss: 0.0198 - val_acc: 0.0000e+00
Epoch 148/200
89/89 [==============================] - 0s 163us/step - loss: 0.0073 - acc: 0.0000e+00 - val_loss: 0.0196 - val_acc: 0.0000e+00
Epoch 149/200
89/89 [==============================] - 0s 163us/step - loss: 0.0070 - acc: 0.0000e+00 - val_loss: 0.0193 - val_acc: 0.0000e+00
Epoch 150/200
89/89 [==============================] - 0s 152us/step - loss: 0.0077 - acc: 0.0000e+00 - val_loss: 0.0195 - val_acc: 0.0000e+00

...

Epoch 37/200
261/261 [==============================] - 23s 87ms/step - loss: 0.0162 - acc: 0.0000e+00 - val_loss: 0.0590 - val_acc: 0.0000e+00
Epoch 38/200
261/261 [==============================] - 23s 87ms/step - loss: 0.0174 - acc: 0.0000e+00 - val_loss: 0.0581 - val_acc: 0.0000e+00
Epoch 39/200
261/261 [==============================] - 22s 86ms/step - loss: 0.0171 - acc: 0.0000e+00 - val_loss: 0.0574 - val_acc: 0.0000e+00
Epoch 40/200
261/261 [==============================] - 24s 90ms/step - loss: 0.0165 - acc: 0.0000e+00 - val_loss: 0.0566 - val_acc: 0.0000e+00
Epoch 41/200
261/261 [==============================] - 25s 95ms/step - loss: 0.0174 - acc: 0.0000e+00 - val_loss: 0.0561 - val_acc: 0.0000e+00
Epoch 42/200
261/261 [==============================] - 24s 90ms/step - loss: 0.0178 - acc: 0.0000e+00 - val_loss: 0.0561 - val_acc: 0.0000e+00
Epoch 43/200
261/261 [==============================] - 24s 90ms/step - loss: 0.0178 - acc: 0.0000e+00 - val_loss: 0.0563 - val_acc: 0.0

Epoch 94/200
261/261 [==============================] - 22s 83ms/step - loss: 0.0170 - acc: 0.0000e+00 - val_loss: 0.0568 - val_acc: 0.0000e+00
Epoch 95/200
261/261 [==============================] - 22s 82ms/step - loss: 0.0166 - acc: 0.0000e+00 - val_loss: 0.0566 - val_acc: 0.0000e+00
Epoch 96/200
261/261 [==============================] - 21s 82ms/step - loss: 0.0170 - acc: 0.0000e+00 - val_loss: 0.0564 - val_acc: 0.0000e+00
Epoch 97/200
261/261 [==============================] - 22s 82ms/step - loss: 0.0168 - acc: 0.0000e+00 - val_loss: 0.0566 - val_acc: 0.0000e+00
Epoch 98/200
261/261 [==============================] - 21s 82ms/step - loss: 0.0167 - acc: 0.0000e+00 - val_loss: 0.0569 - val_acc: 0.0000e+00
Epoch 99/200
261/261 [==============================] - 22s 83ms/step - loss: 0.0164 - acc: 0.0000e+00 - val_loss: 0.0568 - val_acc: 0.0000e+00
Epoch 100/200
261/261 [==============================] - 22s 83ms/step - loss: 0.0162 - acc: 0.0000e+00 - val_loss: 0.0567 - val_acc: 0.

Epoch 151/200
261/261 [==============================] - 22s 85ms/step - loss: 0.0110 - acc: 0.0000e+00 - val_loss: 0.0233 - val_acc: 0.0000e+00
Epoch 152/200
261/261 [==============================] - 22s 84ms/step - loss: 0.0078 - acc: 0.0000e+00 - val_loss: 0.0290 - val_acc: 0.0000e+00
Epoch 153/200
261/261 [==============================] - 22s 84ms/step - loss: 0.0052 - acc: 0.0000e+00 - val_loss: 0.0338 - val_acc: 0.0000e+00
Epoch 154/200
261/261 [==============================] - 22s 86ms/step - loss: 0.0088 - acc: 0.0000e+00 - val_loss: 0.0268 - val_acc: 0.0000e+00
Epoch 155/200
261/261 [==============================] - 23s 87ms/step - loss: 0.0062 - acc: 0.0000e+00 - val_loss: 0.0208 - val_acc: 0.0000e+00
Epoch 156/200
261/261 [==============================] - 22s 85ms/step - loss: 0.0054 - acc: 0.0000e+00 - val_loss: 0.0169 - val_acc: 0.0000e+00
Epoch 157/200
261/261 [==============================] - 23s 88ms/step - loss: 0.0059 - acc: 0.0000e+00 - val_loss: 0.0161 - val_a

Epoch 7/100
176/176 [==============================] - 16s 93ms/step - loss: 0.0650 - acc: 0.0000e+00 - val_loss: 0.0812 - val_acc: 0.0000e+00
Epoch 8/100
176/176 [==============================] - 16s 92ms/step - loss: 0.0334 - acc: 0.0000e+00 - val_loss: 0.0337 - val_acc: 0.0000e+00
Epoch 9/100
176/176 [==============================] - 16s 93ms/step - loss: 0.0155 - acc: 0.0000e+00 - val_loss: 0.0069 - val_acc: 0.0000e+00
Epoch 10/100
176/176 [==============================] - 16s 93ms/step - loss: 0.0175 - acc: 0.0000e+00 - val_loss: 6.1277e-04 - val_acc: 0.0000e+00
Epoch 11/100
176/176 [==============================] - 16s 91ms/step - loss: 0.0318 - acc: 0.0000e+00 - val_loss: 8.6460e-04 - val_acc: 0.0000e+00
Epoch 12/100
176/176 [==============================] - 16s 92ms/step - loss: 0.0389 - acc: 0.0000e+00 - val_loss: 8.3675e-04 - val_acc: 0.0000e+00
Epoch 13/100
176/176 [==============================] - 16s 92ms/step - loss: 0.0391 - acc: 0.0000e+00 - val_loss: 5.1789e-04 -

Epoch 64/100
176/176 [==============================] - 17s 99ms/step - loss: 0.0139 - acc: 0.0000e+00 - val_loss: 0.0224 - val_acc: 0.0000e+00
Epoch 65/100
176/176 [==============================] - 17s 94ms/step - loss: 0.0124 - acc: 0.0000e+00 - val_loss: 0.0233 - val_acc: 0.0000e+00
Epoch 66/100
176/176 [==============================] - 16s 92ms/step - loss: 0.0141 - acc: 0.0000e+00 - val_loss: 0.0241 - val_acc: 0.0000e+00
Epoch 67/100
176/176 [==============================] - 16s 92ms/step - loss: 0.0135 - acc: 0.0000e+00 - val_loss: 0.0245 - val_acc: 0.0000e+00
Epoch 68/100
176/176 [==============================] - 16s 91ms/step - loss: 0.0128 - acc: 0.0000e+00 - val_loss: 0.0247 - val_acc: 0.0000e+00
Epoch 69/100
176/176 [==============================] - 17s 94ms/step - loss: 0.0132 - acc: 0.0000e+00 - val_loss: 0.0246 - val_acc: 0.0000e+00
Epoch 70/100
176/176 [==============================] - 16s 93ms/step - loss: 0.0132 - acc: 0.0000e+00 - val_loss: 0.0243 - val_acc: 0.0